In [1]:
import numpy as np
from scipy.optimize import minimize
import numpy as np

# Define Parameters
lambda_vals = np.array([0.03, 0.04, 0.05, 0.06, 0.07, 1, 1.1, 1.2, 1.3, 1.4, 1.5])  # Request rates ascendingly
N = len(lambda_vals)
B = 4.4  # Cache size
c_delta = 1  # Age linear cost
c_f = 7  # Fetching linear cost (caching miss cost)


In [2]:
import numpy as np

def theoretical_opt(lambda_vals, B, c_f, c_delta):
    """
    Perform theoretical optimization to compute optimal hit probabilities.
    
    Parameters:
    - lambda_vals: Array of request rates.
    - B: Cache size (constraint on total hit probabilities).
    - c_f: Cost of fetching (cache miss cost).
    - c_delta: Cost of caching (hit cost).

    Returns:
    - h_optt: Optimal hit probabilities.
    """
    N = len(lambda_vals)
    h_optt = np.zeros(N)  # Initialize optimal hit probabilities
    differenc_set = np.arange(N)  # Set of variables to optimize
    fix_i = []  # Set of fixed variables (those already optimized)
    n = N
    b = B
    flag = True

    while flag:
        if n == 0:  # If no variables left to optimize
            if b > 0:  # If there is leftover cache size, redistribute it
                differenc_set = np.where(h_optt == 0)[0]  # Find zero hit probability variables
                fix_i = np.setdiff1d(np.arange(N), differenc_set)
                n = len(differenc_set)
                continue
            else:  # No variables to optimize, finalize
                h_optt[differenc_set] = 0
                break
        
        # Calculate the optimal Lagrange multiplier (mu) and hit probabilities for the set of variables
        mu = max(0, (n * c_f - b * c_delta) / np.sum(1 / lambda_vals[differenc_set]))
        h_optt[differenc_set] = (c_f - mu / lambda_vals[differenc_set]) / c_delta
        
        # If mu < 0, adjust the cache size to set mu to zero in the next iteration
        if mu < 0:
            b = (n * c_f / c_delta)
            continue
        
        # Identify violations of the hit probability constraints (h > 1 or h < 0)
        larger_i = np.where(h_optt > 1)[0]
        smaller_i = np.where(h_optt < 0)[0]

        # If no violations, the optimal solution is reached
        if len(smaller_i) == 0 and len(larger_i) == 0:
            break
        
        # Find the furthest object from the boundary (either 0 or 1)
        min_viol = 0
        min_viol_i = -1
        if len(smaller_i) > 0:
            min_viol, min_viol_i = np.min(h_optt[smaller_i]), np.argmin(h_optt[smaller_i])

        max_viol = 0
        max_viol_i = -1
        if len(larger_i) > 0:
            max_viol, max_viol_i = np.max(h_optt[larger_i] - 1), np.argmax(h_optt[larger_i] - 1)
        
        # Choose the variable with the largest violation to adjust
        if max_viol > abs(min_viol):
            viol_i = max_viol_i
            min_viol_flag = 0
        else:
            viol_i = min_viol_i
            min_viol_flag = 1
        
        # Set the furthest object to the nearest boundary (0 or 1)
        if min_viol_flag:
            h_optt[viol_i] = 0
        else:
            h_optt[viol_i] = min(1, b)
        
        # Update cache size and fix the selected variable
        b -= h_optt[viol_i]
        fix_i.append(viol_i)
        differenc_set = np.setdiff1d(np.arange(N), fix_i)
        n = N - len(fix_i)
    
    return h_optt

In [3]:

def numerical_opt(lambda_vals, B, c_f, c_delta):
    """
    Perform numerical optimization to compute optimal hit probabilities.

    Parameters:
    - lambda_vals: Array of request rates.
    - B: Cache size (constraint on total hit probabilities).
    - c_f: Cost of fetching (cache miss cost).
    - c_delta: Cost of caching (hit cost).

    Returns:
    - x_opt: Optimal hit probabilities.
    """
    N = len(lambda_vals)  # Number of items

    # Initial guess: Even distribution of cache capacity
    x_init = np.full(N, B / N)

    # Objective function
    def objective(x):
        return np.sum(lambda_vals * ((1 - x) * c_f + x**2 * c_delta / 2))

    # Constraint: Sum of hit probabilities <= cache size (B)
    def constraint_total_hit(x):
        return B - np.sum(x)  # Non-negative means constraint satisfied

    # Bounds for hit probabilities: 0 <= h_i <= 1
    bounds = [(0, 1) for _ in range(N)]

    # Optimization
    constraints = [{'type': 'ineq', 'fun': constraint_total_hit}]  # Inequality constraint
    result = minimize(
        objective, 
        x_init, 
        method='SLSQP',  # Sequential Least Squares Quadratic Programming
        bounds=bounds, 
        constraints=constraints, 
        options={'disp': True}  # Set to True for optimization output
    )

    # Optimal solution
    if result.success:
        return result.x  # Optimal hit probabilities
    else:
        raise ValueError("Optimization failed: " + result.message)


In [4]:

# Optimization
h_numerical = numerical_opt(lambda_vals, B, c_f, c_delta)
h_theoretical = theoretical_opt(lambda_vals, B, c_f, c_delta)

# Comparison of Hit Probabilities
hit_opt = np.vstack((h_numerical, h_theoretical)).T  # Combine numerical and theoretical hit probabilities

# Objective Function Calculation
obj_1 = np.sum(lambda_vals * ((1 - h_numerical) * c_f + h_numerical**2 * c_delta / 2))
obj_2 = np.sum(lambda_vals * ((1 - h_theoretical) * c_f + h_theoretical**2 * c_delta / 2))
obj = [obj_1, obj_2]  # Store objective function values for both methods

# Constraints
const_1 = np.sum(h_numerical) - B
const_2 = np.sum(h_theoretical) - B
constraint = [const_1, const_2]  # Check if the cache size constraint is satisfied

# Outputs
print("Hit probabilities (numerical and theoretical):\n", hit_opt)
print("Objective function values (numerical, theoretical):", obj)
print("Constraint violations (numerical, theoretical):", constraint)

Optimization terminated successfully    (Exit mode 0)
            Current function value: 16.15721739129548
            Iterations: 4
            Function evaluations: 48
            Gradient evaluations: 4
Hit probabilities (numerical and theoretical):
 [[0.00000000e+00 0.00000000e+00]
 [0.00000000e+00 0.00000000e+00]
 [0.00000000e+00 0.00000000e+00]
 [0.00000000e+00 0.00000000e+00]
 [0.00000000e+00 0.00000000e+00]
 [4.58923826e-13 1.00000000e+00]
 [4.26087031e-01 0.00000000e+00]
 [9.73912969e-01 4.00000000e-01]
 [1.00000000e+00 0.00000000e+00]
 [1.00000000e+00 0.00000000e+00]
 [1.00000000e+00 0.00000000e+00]]
Objective function values (numerical, theoretical): [16.15721739129548, 44.486]
Constraint violations (numerical, theoretical): [1.241673430740775e-12, -3.0]
